# Software Entwicklung 

## Kapitel 9: IO

### 9.5 Sockets

So wie der Begriff *Datei* eine griffige Bezeichnung für eine Ansammlung dauerhaft gespeicherter Bytes ist, wird
mit *Socket* ein Endpunkt für Netzwerkverbindungen bezeichnet.
Die Kommunikation findet zwischen zwei Sockets *bidirektional* statt, d.h. über jedes Socket können Bytes versendet
und empfangen werden.

Sockets stehen in Python durch das Standard-Modul <code>sockets</code> zur Verfügung. Wie schon Dateien belegen auch
Sockets Betriebssystem-Ressourcen, so dass die Verwendung eines Kontextmanagers ratsam ist.

In [ ]:
import socket

with socket.socket() as s:
    pass

#### 9.5.1 Client-Server-Modell

Zwar sind bei einer bestehenden Kommunikationsverbindung zwischen zwei Sockets die beiden Sockets prinzipiell
gleichberechtigt, jedoch gibt es Unterschiede beim Kommunikationsaufbau.

* Ein *Server-Socket* verhält sich passiv, d.h. es wartet auf eingehende Verbindungsanfragen. Trifft eine solche
  ein, generiert es ein weiteres Socket, das fest dieser Verbindung zugeordnet wird und über das die
  anschließende Kommunikation abgewickelt wird. Das *Server-Socket* selbst verbleibt im Wartezustand.

* Ein *Client-Socket* übernimmt den aktiven Part. Es kontaktiert das *Server-Socket* und geht selbst die
  Verbindung mit dem daraufhin bereitgestellten Socket ein.

Die Verbindungsaufnahme folgt einem vorgegebenen Ablauf aus definierten Schritten (auch: *Kommunikationsprimitive*).

![Verbindungsaufnahme mit Kommunkationsprimitiven](../img/Primitive.png "Kommunikationsprimitive")

#### 9.5.2 Server-Socket

Ein *Server-Socket* ist eindeutig festgelegt durch das Protokoll (z.B. TCP oder UDP), den Rechner
(z.B. durch dessen IP-Adresse) und eine Portnummer. Letztere dient dazu, dass mehrere Server-Sockets gleichzeitig
auf einem Rechner existieren können, ohne sich gegenseitig zu beeinflussen.

So gibt es z.B. auf dem Server <code>medinf.efi.th-nuernberg.de</code> mehrere Server-Sockets,
die permanent angesprochen werden können:

* Port 22: Nimmt Secure-Shell-Anfragen entgegen
* Port 80: Nimmt HTTP-Anfragen entgegen
* Port 443: Nimmt HTTPS-Anfragen entgegen

Das *Server-Socket* wird mit <code>bind</code> an einen bestimmten Port und eine
IP-Adresse (ggf. hat ein Rechner mehrere IP-Adressen) gebunden. Das Binden schlägt fehl, wenn die
Kombination bereits von einem anderen Socket belegt ist.

Anschließend beginnt das *Server-Socket* mit <code>listen</code> zu lauschen. Das Primitiv <code>accept</code>
blockiert den Server, bis ein *Client-Socket* Verbindung aufnimmt. Damit entsteht ein weiteres Socket mit
einer vom System vergebenen Portnummer, das dediziert nur für die Verbindung mit diesem Client verwendet wird.

Über dieses neue Socket folgen danach Primitive zum Senden
<code>send</code> und Empfangen <code>receive</code> von Nachrichten. Anzahl und Abfolge sind
für Sockets nicht festgelegt, müssen aber zwischen Client und Server abgestimmt sein. So legt z.B.
das auf Sockets aufsetzende Protokoll HTTP fest, dass zunächst eine Nachricht vom Client
an den Server (*HTTP-Request*) und anschließend eine Nachricht vom Server an den Client
(*HTTP-Response*) gesendet wird. Während in der ersten Version von HTTP danach die
Verbindung wieder abgebaut wurde, ist es aktuellen Versionen möglich, dieses Abfolge
wiederholt über eine bestehende Verbindung abzuwickeln.

Eine etablierte Verbindung ist mit <code>close</code> zu schließen. Bei Verwendung eines
Kontextmanagers erfolgt dies automatisch.

Auch das *Server-Socket* muss geschlossen werden, um das Binden an einen Port zu beenden
und den Port freizugeben.